In [1]:
import sqlite3
import pandas as pd

db_path = "synapse_predictions.db"

conn = sqlite3.connect(db_path)

query = """
SELECT 
    pre.id AS pre_id,
    pre.score,
    pre.z AS pre_z,
    pre.y AS pre_y,
    pre.x AS pre_x,
    post.id AS post_id,
    post.z AS post_z,
    post.y AS post_y,
    post.x AS post_x
FROM pre_sites pre
JOIN pre_post_mapping map ON pre.id = map.pre_id
JOIN post_sites post ON post.id = map.post_id
"""

df = pd.read_sql_query(query, conn)
conn.close()

df.head()


pre_id        score  pre_z     pre_y     pre_x  post_id  post_z    post_y  \
0       1   160.809753  448.0   57192.0  106304.0        2   576.0   57272.0   
1       3   464.014526  864.0   59704.0  115880.0        4   784.0   59688.0   
2       5  7256.042480  432.0  114024.0   81128.0        6   336.0  113944.0   
3       7   150.132629  672.0   65064.0  115768.0        8   640.0   65080.0   
4       9  2096.442383  216.0   81296.0  112960.0       10   232.0   81400.0   

     post_x  
0  106656.0  
1  115896.0  
2   81248.0  
3  115648.0  
4  113168.0

In [33]:
df1 = df[(df["pre_z"] >= 60000) & (df["pre_z"] < 70000)].copy()
df1.head()

pre_id        score    pre_z    pre_y     pre_x  post_id   post_z  \
1332150  2664301   640.651611  60032.0  41176.0   33576.0  2664302  59896.0   
1332151  2664303   348.536011  60032.0  41128.0   33576.0  2664304  59896.0   
1332362  2664725   425.261047  60000.0  40856.0  130664.0  2664726  59888.0   
1332543  2665087  1328.277222  60056.0  28864.0   52256.0  2665088  59896.0   
1332576  2665153   315.221588  60024.0  28896.0   37760.0  2665154  59864.0   

          post_y    post_x  
1332150  41000.0   33584.0  
1332151  41176.0   33640.0  
1332362  40872.0  130656.0  
1332543  28792.0   52312.0  
1332576  28968.0   37728.0

In [6]:
import pymaid

url = "https://neurophyla.mrc-lmb.cam.ac.uk/catmaid/fibsem/#"
token = "4fe0c0572331265c61bf6ba4acd77cbed9792276"
name = "SYLee"
password = "Blue Skies"
project_id = 32
rm = pymaid.CatmaidInstance(url, token, name, password, project_id)

INFO  : Global CATMAID instance set. Caching is ON. (pymaid)


In [37]:
df_test = df1.iloc[:5].copy()
df_test

pre_id        score    pre_z    pre_y     pre_x  post_id   post_z  \
11687   23375  4765.322754  20000.0  79280.0  127488.0    23376  19960.0   
11690   23381   138.847900  20032.0  79224.0  127528.0    23382  19912.0   
11691   23383   458.006897  20040.0  79232.0  127496.0    23384  19944.0   
11696   23393   274.688538  20000.0  79440.0  114424.0    23394  19960.0   
11725   23451   874.418274  20088.0  95376.0   96528.0    23452  19960.0   

        post_y    post_x  
11687  79296.0  127464.0  
11690  79120.0  127528.0  
11691  79160.0  127432.0  
11696  79400.0  114448.0  
11725  95432.0   96456.0

In [44]:
 import time
import sqlite3
import pandas as pd
import json

DB_PATH = "push_results_60k_70k_round3.sqlite"
TABLE = "push_log"

CHUNK_SIZE = 5000       # increase later (1000–5000)
RETRIES = 3
SLEEP_BASE = 1.0

required_cols = ["post_id", "post_x", "post_y", "post_z", "pre_x", "pre_y", "pre_z"]
missing = [c for c in required_cols if c not in df1.columns]
if missing:
    raise ValueError(f"Missing required columns: {missing}")

def retry_call(fn, *args, retries=RETRIES, **kwargs):
    last_err = None
    for attempt in range(retries):
        try:
            return fn(*args, **kwargs), None
        except Exception as e:
            last_err = e
            time.sleep(SLEEP_BASE * (2 ** attempt))
    return None, repr(last_err)

def resp_error(resp):
    # pymaid sometimes returns dict with {"error": "..."}
    if isinstance(resp, dict) and resp.get("error"):
        return resp.get("error")
    return None

def normalize_int(x):
    if x is None:
        return None
    try:
        return int(x)
    except Exception:
        return None

def to_json_text(x):
    if x is None:
        return None
    try:
        return json.dumps(x)
    except Exception:
        return str(x)

def first_dict_from_response(resp):
    """
    Normalize pymaid responses:
    - if resp is a list like [ {...} ], return the first dict
    - if resp is a dict, return it
    - else return {}
    """
    if isinstance(resp, list) and len(resp) > 0 and isinstance(resp[0], dict):
        return resp[0]
    if isinstance(resp, dict):
        return resp
    return {}

# --- SQLite setup ---
conn = sqlite3.connect(DB_PATH)
conn.execute(f"""
CREATE TABLE IF NOT EXISTS {TABLE} (
  idx INTEGER,
  post_id INTEGER,

  pre_x REAL, pre_y REAL, pre_z REAL,
  post_x REAL, post_y REAL, post_z REAL,

  treenode_id INTEGER,
  skeleton_id INTEGER,
  edition_time TEXT,
  node_error TEXT,

  connector_id INTEGER,
  connector_edition_time TEXT,
  created_links TEXT,
  connector_error TEXT,

  linked_ok INTEGER,
  link_error TEXT
)
""")
conn.commit()

def process_chunk(chunk: pd.DataFrame, print_link_response=False):
    rows_out = []
    links = []
    link_row_idxs = []

    for r in chunk.itertuples(index=True):
        idx = int(r.Index)

        post_id = normalize_int(r.post_id)
        pre_x, pre_y, pre_z = float(r.pre_x), float(r.pre_y), float(r.pre_z)
        post_x, post_y, post_z = float(r.post_x), float(r.post_y), float(r.post_z)

        # 1) add node (NOTE: will fail with your CATMAID 'skeleton' issue if parent_id=None)
        node_resp_raw, node_exc = retry_call(
            pymaid.add_node,
            (post_x, post_y, post_z),
            parent_id=None,
            radius=-1,
            confidence=5,
        )
        node_resp = first_dict_from_response(node_resp_raw)
        node_err = node_exc or resp_error(node_resp)

        treenode_id = normalize_int(node_resp.get("treenode_id") or node_resp.get("id")) if node_err is None else None
        skeleton_id  = normalize_int(node_resp.get("skeleton_id")) if node_err is None else None
        edition_time = node_resp.get("edition_time") if node_err is None else None

        # 2) add connector (YOUR CASE: returns a list with first dict)
        connector_id = None
        connector_edition_time = None
        created_links = None
        conn_err = None

        # If you want to create connectors even when node creation fails, remove this condition.
        if treenode_id is not None:
            conn_resp_raw, conn_exc = retry_call(
                pymaid.add_connector,
                (pre_x, pre_y, pre_z),
                remote_instance=None
            )
            conn_resp = first_dict_from_response(conn_resp_raw)
            conn_err = conn_exc or resp_error(conn_resp)

            if conn_err is None:
                connector_id = normalize_int(conn_resp.get("connector_id") or conn_resp.get("id") or conn_resp.get("new_connector_id"))
                connector_edition_time = conn_resp.get("connector_edition_time")
                created_links = conn_resp.get("created_links")

                if connector_id is None:
                    conn_err = f"Connector created but connector_id missing. Keys={list(conn_resp.keys())}"

        # record row
        rows_out.append({
            "idx": idx,
            "post_id": post_id,

            "pre_x": pre_x, "pre_y": pre_y, "pre_z": pre_z,
            "post_x": post_x, "post_y": post_y, "post_z": post_z,

            "treenode_id": treenode_id,
            "skeleton_id": skeleton_id,
            "connector_id": connector_id,
            "edition_time": edition_time,
            "node_error": node_err,      

            "linked_ok": 0,
            "link_error": None,
        })

        rows_out.append({
            "idx": idx,
            "post_id": post_id,

            "pre_x": pre_x, "pre_y": pre_y, "pre_z": pre_z,
            "post_x": post_x, "post_y": post_y, "post_z": post_z,

            "treenode_id": treenode_id,
            "skeleton_id": skeleton_id,      
            "edition_time": edition_time,   
            "node_error": node_err,

            "connector_id": connector_id,

            "linked_ok": 0,
            "link_error": None,
        })

        # 3) prepare link
        if treenode_id is not None and connector_id is not None:
            links.append((treenode_id, connector_id, "postsynaptic_to"))
            link_row_idxs.append(len(rows_out) - 1)

    # 3) link once per chunk
    if links:
        link_resp_raw, link_exc = retry_call(pymaid.link_connector, links)

        if print_link_response:
            print("LINK RESPONSE:", link_resp_raw)

        # Expect list of dicts with message == 'success'
        if link_exc is None and isinstance(link_resp_raw, list):
            for j, item in enumerate(link_resp_raw):
                row_i = link_row_idxs[j] if j < len(link_row_idxs) else None
                if row_i is None:
                    continue
                ok = isinstance(item, dict) and item.get("message") == "success"
                rows_out[row_i]["linked_ok"] = 1 if ok else 0
                if not ok:
                    rows_out[row_i]["link_error"] = str(item)
        else:
            # error or unexpected shape
            err = link_exc or str(link_resp_raw)
            for row_i in link_row_idxs:
                rows_out[row_i]["linked_ok"] = 0
                rows_out[row_i]["link_error"] = err

    pd.DataFrame(rows_out).to_sql(TABLE, conn, if_exists="append", index=False)


for start in range(0, len(df1), CHUNK_SIZE):
    process_chunk(df1.iloc[start:start + CHUNK_SIZE], print_link_response=True)
    conn.commit()
    print(f"Processed rows {start}..{start + len(df1.iloc[start:start + CHUNK_SIZE]) - 1}")

conn.close()
print("Done. Logged to:", DB_PATH)


Creating connectors: 0it [00:00, ?it/s]

Creating connectors: 0it [00:00, ?it/s]

Creating connectors: 0it [00:00, ?it/s]

Creating connectors: 0it [00:00, ?it/s]

Creating connectors: 0it [00:00, ?it/s]

...

Creating connectors: 0it [00:00, ?it/s]

Creating connectors: 0it [00:00, ?it/s]

Creating connectors: 0it [00:00, ?it/s]

Linking connectors:   0%|          | 0/2701 [00:00<?, ?it/s]

LINK RESPONSE: [{'message': 'success', 'link_id': 31640714, 'link_edition_time': '2026-01-16T11:54:45.452Z', 'relation_id': 22238449}, {'message': 'success', 'link_id': 31640717, 'link_edition_time': '2026-01-16T11:54:45.469Z', 'relation_id': 22238449}, {'message': 'success', 'link_id': 31640720, 'link_edition_time': '2026-01-16T11:54:45.472Z', 'relation_id': 22238449}, {'message': 'success', 'link_id': 31640718, 'link_edition_time': '2026-01-16T11:54:45.471Z', 'relation_id': 22238449}, {'message': 'success', 'link_id': 31640716, 'link_edition_time': '2026-01-16T11:54:45.462Z', 'relation_id': 22238449}, {'message': 'success', 'link_id': 31640719, 'link_edition_time': '2026-01-16T11:54:45.473Z', 'relation_id': 22238449}, {'message': 'success', 'link_id': 31640715, 'link_edition_time': '2026-01-16T11:54:45.470Z', 'relation_id': 22238449}, {'message': 'success', 'link_id': 31640722, 'link_edition_time': '2026-01-16T11:54:45.503Z', 'relation_id': 22238449}, {'message': 'success', 'link_id'

In [41]:
import sqlite3, pandas as pd

conn = sqlite3.connect("push_results_60k_70k_round2.sqlite")
df_db = pd.read_sql_query("SELECT * FROM push_log ORDER BY rowid DESC LIMIT 10", conn)
conn.close()

display(df_db)


idx  post_id     pre_x     pre_y    pre_z    post_x    post_y   post_z  \
0  1783263  3566528   80144.0  115952.0  68248.0   80176.0  116104.0  68312.0   
1  1783263  3566528   80144.0  115952.0  68248.0   80176.0  116104.0  68312.0   
2  1783262  3566526   80152.0  115984.0  68192.0   80064.0  116096.0  68296.0   
3  1783262  3566526   80152.0  115984.0  68192.0   80064.0  116096.0  68296.0   
4  1783261  3566524   40880.0  115800.0  68864.0   40808.0  115648.0  68824.0   
5  1783261  3566524   40880.0  115800.0  68864.0   40808.0  115648.0  68824.0   
6  1783260  3566522   28504.0  115912.0  68872.0   28512.0  115856.0  68720.0   
7  1783260  3566522   28504.0  115912.0  68872.0   28512.0  115856.0  68720.0   
8  1783259  3566520  113312.0  116376.0  68672.0  113328.0  116232.0  68808.0   
9  1783259  3566520  113312.0  116376.0  68672.0  113328.0  116232.0  68808.0   

   treenode_id  skeleton_id              edition_time node_error  \
0     57703938     31389400  2026-01-15T16:57:46.495Z       None   
1     57703938     31389400  2026-01-15T16:57:46.495Z       None   
2     57703936     31389396  2026-01-15T16:57:46.394Z       None   
3     57703936     31389396  2026-01-15T16:57:46.394Z       None   
4     57703934     31389392  2026-01-15T16:57:46.314Z       None   
5     57703934     31389392  2026-01-15T16:57:46.314Z       None   
6     57703932     31389388  2026-01-15T16:57:46.244Z       None   
7     57703932     31389388  2026-01-15T16:57:46.244Z       None   
8     57703930     31389384  2026-01-15T16:57:46.168Z       None   
9     57703930     31389384  2026-01-15T16:57:46.168Z       None   

   connector_id connector_edition_time created_links connector_error  \
0      57703939                   None          None            None   
1      57703939                   None          None            None   
2      57703937                   None          None            None   
3      57703937                   None          None            None   
4      57703935                   None          None            None   
5      57703935                   None          None            None   
6      57703933                   None          None            None   
7      57703933                   None          None            None   
8      57703931                   None          None            None   
9      57703931                   None          None            None   

   linked_ok link_error  
0          1       None  
1          0       None  
2          1       None  
3          0       None  
4          1       None  
5          0       None  
6          1       None  
7          0       None  
8          1       None  
9          0       None

In [42]:
resume_from = 1783263  # last processed
df_resume = df1.loc[df1.index > resume_from].copy()

print("Resuming from idx >", resume_from)
print("Remaining rows:", len(df_resume))
print("Next idx:", df_resume.index.min() if len(df_resume) else None)


Resuming from idx > 1783263
Remaining rows: 37701
Next idx: 1783264


In [43]:
df1 = df_resume.copy()
df1

pre_id        score    pre_z     pre_y    pre_x  post_id   post_z  \
1783264  3566529   169.396027  68344.0  115912.0  80216.0  3566530  68384.0   
1783265  3566531   655.322327  68272.0  115968.0  80184.0  3566532  68408.0   
1783266  3566533  1364.702637  69096.0  115616.0  80128.0  3566534  68856.0   
1783267  3566535  1040.677612  69048.0  115592.0  80112.0  3566536  69016.0   
1783268  3566537  1305.438477  69056.0  115640.0  80128.0  3566538  68968.0   
...          ...          ...      ...       ...      ...      ...      ...   
1843127  3686255  2059.200195  69968.0  124936.0  55024.0  3686256  70040.0   
1843128  3686257   291.115601  69936.0  124984.0  55096.0  3686258  69888.0   
1843129  3686259   792.930237  69888.0  124952.0  55112.0  3686260  69960.0   
1843130  3686261   414.094299  69944.0  124896.0  55024.0  3686262  70128.0   
1843133  3686267   544.676941  69864.0  157512.0  45080.0  3686268  70000.0   

           post_y   post_x  
1783264  116096.0  80328.0  
1783265  116024.0  80184.0  
1783266  115648.0  80112.0  
1783267  115888.0  80112.0  
1783268  115728.0  80048.0  
...           ...      ...  
1843127  124832.0  55144.0  
1843128  124872.0  55208.0  
1843129  125008.0  55248.0  
1843130  124888.0  55016.0  
1843133  157344.0  45184.0  

[37701 rows x 9 columns]